In [1]:
from datasets import Dataset
from distilabel.llm import OpenAILLM
from distilabel.pipeline import Pipeline

from dotenv import load_dotenv

load_dotenv("../.env")


/home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


True

# Self Instruct

In [136]:
use_cases = [
    "User representation: A user profile is represented as a JSON schema.",
    "User representation: A user profile is represented as a Pydantic class.",
    "Company representation: A company profile is represented as a Pydantic class.",
    "Message representation: A message is represented as a Pydantic class.",
    "Booking representation: A booking is represented as a Pydantic class.",
    "Novel representation: A novel is represented as a Pydantic class.",
    "Author representation: An author is represented as a Pydantic class.",
    "Software representation: A software application is represented as a Pydantic class.",
]

use_case_dataset = Dataset.from_dict({"input": use_cases})

# JSON Generation task

In [32]:
import json

from typing import Dict

from distilabel.tasks import TextGenerationTask

In [12]:
use_cases = [
    "User representation: A user profile is represented as a JSON schema.",
]
use_case_dataset = Dataset.from_dict({"input": use_cases})

In [98]:
class JsonTask(TextGenerationTask):
    system_prompt = "You are an AI assistant that responds only using JSON structures, no explanation or anything else that isn't a JSON."

    @property
    def output_args_names(self):
        return ["generations"]

    def parse_output(self, output: str) -> Dict[str, str]:
        json.loads(output)
        return {"generations": output}
    
generator_task = JsonTask(
    system_prompt = (
        "You an expert JSON schema developer, specialising in robust JSON schemas."
        "You are given a use case for a specific software application entity."
        "You represent the software application entity as as JSON schemas."
        "You write only JSON schemas and do not introduce the code with prose."
        ),
)
instruction_generator = OpenAILLM(
    task=generator_task,
    num_threads=1,
    max_new_tokens=1024,
    model="gpt-3.5-turbo",
)

In [99]:
num_generations = 1
batch_size = 1
pipeline = Pipeline(generator=instruction_generator)
distiset = pipeline.generate(
    dataset=use_case_dataset, num_generations=num_generations, batch_size=batch_size
)

14:26:55 INFO     [PID: 223803] Executing dry-run...                                                ]8;id=747665;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=933807;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py#747\747]8;;\

         INFO     [PID: 223803] Processing batch 1 of 1...                                          ]8;id=908781;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=834078;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py#569\569]8;;\

         INFO     [PID: 223803] Calling generator for batch 1...                                    ]8;id=837889;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=54780;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py#573\573]8;;\

Flattening the indices: 100%|██████████| 1/1 [00:00<00:00, 637.04 examples/s]


14:27:03 INFO     [PID: 223803] Dry-run executed with no issues. Starting the actual generation...  ]8;id=28911;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=585204;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py#749\749]8;;\

/home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/rich/live.py:231: UserWarning: install 
"ipywidgets" for Jupyter support
  warnings.warn('install "ipywidgets" for Jupyter support')

         INFO     [PID: 223803] Processing batch 1 of 1...                                          ]8;id=744892;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=965854;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py#569\569]8;;\

         INFO     [PID: 223803] Calling generator for batch 1...                                    ]8;id=981264;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=934191;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py#573\573]8;;\

Saving the dataset (1/1 shards): 100%|██████████| 1/1 [00:00<00:00, 321.13 examples/s]


14:27:10 INFO     [PID: 223803] Final dataset saved at /home/ben/code/instructdantic/notebooks/ckpt ]8;id=878176;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=828682;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py#658\658]8;;\

In [100]:
distiset

Dataset({
    features: ['input', 'generation_model', 'generation_prompt', 'raw_generation_responses', 'generations'],
    num_rows: 1
})

In [101]:
from rich import print
# get a sample and log it clearly
prompt_samples = [sample["generation_prompt"] for sample in distiset][0][0]
raw_generation_responses = distiset["generations"][0][0]

for p in prompt_samples:
    print(p)
print(raw_generation_responses)

{
    'content': 'You an expert JSON schema developer, specialising in robust JSON schemas.You are given a use case 
for a specific software application entity.You represent the software application entity as as JSON schemas.You 
write only JSON schemas and do not introduce the code with prose.',
    'role': 'system'
}

{'content': 'User representation: A user profile is represented as a JSON schema.', 'role': 'user'}

{
  "$schema": "http://json-schema.org/draft-07/schema#",
  "title": "User Profile",
  "type": "object",
  "properties": {
    "id": {
      "type": "string",
      "format": "uuid"
    },
    "username": {
      "type": "string"
    },
    "email": {
      "type": "string",
      "format": "email"
    },
    "firstName": {
      "type": "string"
    },
    "lastName": {
      "type": "string"
    },
    "dateOfBirth": {
      "type": "string",
      "format": "date"
    },
    "address": {
      "type": "object",
      "properties": {
        "street": {
          "type": "string"
        },
        "city": {
          "type": "string"
        },
        "state": {
          "type": "string"
        },
        "country": {
          "type": "string"
        },
        "postalCode": {
          "type": "string"
        }
      },
      "required": ["street", "city", "country", "postalCode"]
    },
    "phoneNumbers": {
      "type": "array",
      "items": {
        "type": "object",
        "properties": {
          "type": {
            "type": "string",
            "enum": ["home", "work", "mobile"]
          },
          "number": {
            "type": "string"
          }
        },
        "required": ["type", "number"]
      }
    },
    "isActive": {
      "type": "boolean"
    },
    "createdAt": {
      "type": "string",
      "format": "date-time"
    },
    "updatedAt": {
      "type": "string",
      "format": "date-time"
    }
  },
  "required": ["id", "username", "email", "firstName", "lastName"]
}

In [102]:
import json

json.loads(raw_generation_responses)

{'$schema': 'http://json-schema.org/draft-07/schema#',
 'title': 'User Profile',
 'type': 'object',
 'properties': {'id': {'type': 'string', 'format': 'uuid'},
  'username': {'type': 'string'},
  'email': {'type': 'string', 'format': 'email'},
  'firstName': {'type': 'string'},
  'lastName': {'type': 'string'},
  'dateOfBirth': {'type': 'string', 'format': 'date'},
  'address': {'type': 'object',
   'properties': {'street': {'type': 'string'},
    'city': {'type': 'string'},
    'state': {'type': 'string'},
    'country': {'type': 'string'},
    'postalCode': {'type': 'string'}},
   'required': ['street', 'city', 'country', 'postalCode']},
  'phoneNumbers': {'type': 'array',
   'items': {'type': 'object',
    'properties': {'type': {'type': 'string',
      'enum': ['home', 'work', 'mobile']},
     'number': {'type': 'string'}},
    'required': ['type', 'number']}},
  'isActive': {'type': 'boolean'},
  'createdAt': {'type': 'string', 'format': 'date-time'},
  'updatedAt': {'type': 'stri

# Use a labeller to judge the quality of the generated JSONs

In [103]:
from textwrap import dedent

from distilabel.tasks.preference.ultrafeedback import Rating, UltraFeedbackTask

task_description = dedent(
    """
    # JSON Schema Validity Assessment
    Evaluate the model's json schema based on various criteria:
    1. **Correctness**: Does the output provide accurate and relevant examples within the JSON fields?
    2. **Instruction Following**: Does the JSON align with given instructions and the user's intent?
    3. **Completeness**: Does the JSON schema represent the instruction fully?

    **Scoring**: Rate outputs 1 to 3 based on the overall quality, considering all aspects:
    """
)

ratings = [
    Rating(value=1, description="The JSON schema is incomplete and does not represent the instruction."),
    Rating(value=2, description="The JSON schema is complete but field, descriptions, and examples should be improved."),
    Rating(value=3, description="The JSON schema is complete and represents the instruction fully."),
]

ultrafeedback_task = UltraFeedbackTask(
    system_prompt="Your role is to evaluate text quality based on given criteria",
    task_description=task_description,
    ratings=ratings,
)

In [104]:
labeller = OpenAILLM(
    task=ultrafeedback_task,
    num_threads=1,
    max_new_tokens=1024,
    model="gpt-4",
)

In [105]:
generator_task = JsonTask(
    system_prompt = (
        "You an expert JSON schema developer, specialising in robust JSON schemas."
        "You are given a use case for a specific software application entity."
        "You represent the software application entity as as JSON schemas."
        "You write only JSON schemas and do not introduce the code with prose."
        ),
)
instruction_generator = OpenAILLM(
    task=generator_task,
    num_threads=1,
    max_new_tokens=1024,
    model="gpt-3.5-turbo",
)

pipeline = Pipeline(generator=instruction_generator, labeller=labeller)

In [137]:
num_generations = 10
batch_size = 10
distiset = pipeline.generate(
    dataset=use_case_dataset, num_generations=num_generations, batch_size=batch_size
)

15:11:03 INFO     [PID: 223803] Executing dry-run...                                                ]8;id=54188;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=362953;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py#747\747]8;;\

/home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py:680: UserWarning: Provided `num_generations=1` which implies that the `generator` LLM will just run once, while the `labelling` LLM expects to receive a list of N inputs to label, where N is > 1. If this is not intended, make sure to set `num_generations` to a value higher or equal to 2.
  return self._generate(


         INFO     [PID: 223803] Processing batch 1 of 1...                                          ]8;id=818337;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=613173;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py#569\569]8;;\

         INFO     [PID: 223803] Calling generator for batch 1...                                    ]8;id=923907;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=371008;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py#573\573]8;;\

15:11:09 INFO     [PID: 223803] Calling labeller for batch 1...                                     ]8;id=50033;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=356747;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/distilabel/pipeline.py#604\604]8;;\

...

15:33:54 INFO     [PID: 223803] Retrying request to /chat/completions in 6.745703 seconds       ]8;id=47236;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/openai/_base_client.py\_base_client.py]8;;\:]8;id=56678;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/openai/_base_client.py#987\987]8;;\

15:34:51 INFO     [PID: 223803] Retrying request to /chat/completions in 7.448612 seconds       ]8;id=563381;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/openai/_base_client.py\_base_client.py]8;;\:]8;id=538531;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/openai/_base_client.py#987\987]8;;\

15:35:49 ERROR    [PID: 223803] exception calling callback for <Future at 0x7f26a6f92ed0               ]8;id=940786;file:///home/ben/anaconda3/lib/python3.11/concurrent/futures/_base.py\_base.py]8;;\:]8;id=877499;file:///home/ben/anaconda3/lib/python3.11/concurrent/futures/_base.py#342\342]8;;\
                  state=finished raised APITimeoutError>                                                           
                  ╭─────────────────────── Traceback (most recent call last) ────────────────────────╮             
                  │ /home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/httpcore/_excep │             
                  │ tions.py:10 in map_exceptions                                                    │             
                  │                                                                                  │             
                  │    7 @contextlib.contextmanager                                                  │             
                  │    8 def map_exceptions(map: ExceptionMapping) -> Iterator[None]:                │             
                  │    9 │   try:                                                                    │             
                  │ ❱ 10 │   │   yield                                                               │             
                  │   11 │   except Exception as exc:  # noqa: PIE786                                │             
                  │   12 │   │   for from_exc, to_exc in map.items():                                │             
                  │   13 │   │   │   if isinstance(exc, from_exc):                                   │             
                  │                                                                                  │             
                  │ ╭──────────────────────────────── locals ────────────────────────────────╮       │             
                  │ │ from_exc = <class 'TimeoutError'>                                      │       │             
                  │ │      map = {                                                           │       │             
                  │ │            │   <class 'TimeoutError'>: <class 'httpcore.ReadTimeout'>, │       │             
                  │ │            │   <class 'OSError'>: <class 'httpcore.ReadError'>         │       │             
                  │ │            }                                                           │       │             
                  │ │   to_exc = <class 'httpcore.ReadTimeout'>                              │       │             
                  │ ╰────────────────────────────────────────────────────────────────────────╯       │             
                  │                                                                                  │             
                  │ /home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/httpcore/_backe │             
                  │ nds/sync.py:126 in read                                                          │             
                  │                                                                                  │             
                  │   123 │   │   exc_map: ExceptionMapping = {socket.timeout: ReadTimeout, OSError: │             
                  │   124 │   │   with map_exceptions(exc_map):                                      │             
                  │   125 │   │   │   self._sock.settimeout(timeout)                                 │             
                  │ ❱ 126 │   │   │   return self._sock.recv(max_bytes)                              │             
                  │   127 │                                                                          │             
                  │   128 │   def write(self, buffer: bytes, timeout: typing.Optional[float] = None) │             
                  │   129 │   │   if not buffer:                                                    

15:36:42 INFO     [PID: 223803] Retrying request to /chat/completions in 0.852356 seconds       ]8;id=674013;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/openai/_base_client.py\_base_client.py]8;;\:]8;id=20088;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/openai/_base_client.py#987\987]8;;\

15:37:33 INFO     [PID: 223803] Retrying request to /chat/completions in 1.983365 seconds       ]8;id=623569;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/openai/_base_client.py\_base_client.py]8;;\:]8;id=697764;file:///home/ben/code/instructdantic/.venv/lib/python3.11/site-packages/openai/_base_client.py#987\987]8;;\

In [107]:
distiset

Dataset({
    features: ['input', 'generation_model', 'generation_prompt', 'raw_generation_responses', 'generations', 'labelling_model', 'labelling_prompt', 'raw_labelling_response', 'rating', 'rationale'],
    num_rows: 1
})

In [110]:
print(
    distiset["generation_prompt"],
    distiset["generations"],
    distiset["raw_labelling_response"],
    distiset["rating"],
    sep="\n",
)

[
    [
        [
            {
                'content': 'You an expert JSON schema developer, specialising in robust JSON schemas.You are given 
a use case for a specific software application entity.You represent the software application entity as as JSON 
schemas.You write only JSON schemas and do not introduce the code with prose.',
                'role': 'system'
            },
            {'content': 'User representation: A user profile is represented as a JSON schema.', 'role': 'user'}
        ],
        [
            {
                'content': 'You an expert JSON schema developer, specialising in robust JSON schemas.You are given 
a use case for a specific software application entity.You represent the software application entity as as JSON 
schemas.You write only JSON schemas and do not introduce the code with prose.',
                'role': 'system'
            },
            {'content': 'User representation: A user profile is represented as a JSON schema.', 'role': 'user'}
        ]
    ]
]
[
    [
        '{\n  "$schema": "http://json-schema.org/draft-07/schema#",\n  "type": "object",\n  "properties": {\n    
"id": {\n      "type": "string",\n      "format": "uuid"\n    },\n    "username": {\n      "type": "string"\n    
},\n    "firstName": {\n      "type": "string"\n    },\n    "lastName": {\n      "type": "string"\n    },\n    
"email": {\n      "type": "string",\n      "format": "email"\n    },\n    "age": {\n      "type": "integer",\n     
"minimum": 18\n    },\n    "address": {\n      "type": "object",\n      "properties": {\n        "street": {\n     
"type": "string"\n        },\n        "city": {\n          "type": "string"\n        },\n        "state": {\n      
"type": "string"\n        },\n        "zipCode": {\n          "type": "string"\n        }\n      },\n      
"required": ["street", "city", "state", "zipCode"]\n    }\n  },\n  "required": ["id", "username", "email"]\n}',
        '{\n  "$schema": "http://json-schema.org/draft-07/schema#",\n  "title": "User Profile",\n  "type": 
"object",\n  "properties": {\n    "id": {\n      "type": "string",\n      "format": "uuid"\n    },\n    
"firstName": {\n      "type": "string",\n      "minLength": 1,\n      "maxLength": 50\n    },\n    "lastName": {\n 
"type": "string",\n      "minLength": 1,\n      "maxLength": 50\n    },\n    "email": {\n      "type": "string",\n 
"format": "email"\n    },\n    "username": {\n      "type": "string",\n      "minLength": 3,\n      "maxLength": 
20\n    },\n    "password": {\n      "type": "string",\n      "minLength": 8,\n      "maxLength": 256\n    },\n    
"dateOfBirth": {\n      "type": "string",\n      "format": "date"\n    },\n    "phone": {\n      "type": 
"string",\n      "pattern": "^[0-9]{10}$"\n    },\n    "address": {\n      "type": "object",\n      "properties": 
{\n        "street": {\n          "type": "string"\n        },\n        "city": {\n          "type": "string"\n    
},\n        "state": {\n          "type": "string"\n        },\n        "country": {\n          "type": "string"\n 
},\n        "zipCode": {\n          "type": "string"\n        }\n      },\n      "required": ["street", "city", 
"state", "country", "zipCode"]\n    }\n  },\n  "required": ["firstName", "lastName", "email", "username", 
"password", "dateOfBirth", "phone", "address"]\n}'
    ]
]
[
    '#### Output for Text 1\nRating: 3\nRationale: The JSON schema aligns well with the instructions and represents
a user profile correctly. It covers various important attributes like id, username, names, email, age, and address,
and correctly defines the required parameters.\n\n#### Output for Text 2\nRating: 3\nRationale: This JSON schema 
also provides a full representation of a user profile consistent with the task instruction. The elements are clear 
and relevant with good examples like defining the id format as uuid and having set parameters like minimum and 
maximum string lengths for appropriate fields. It covers a more detailed user pr

# use agent tools

In [115]:
from langchain import hub
from langchain.agents import AgentExecutor
from langchain_experimental.tools import PythonREPLTool

In [116]:
tools = [PythonREPLTool()]

In [117]:
from langchain.agents import create_openai_functions_agent
from langchain_openai import ChatOpenAI

In [119]:
instructions = """You are an agent designed to write and execute python code to answer questions.
You have access to a python REPL, which you can use to execute python code.
If you get an error, debug your code and try again.
Only use the output of your code to answer the question. 
You might know the answer without running any code, but you should still run the code to get the answer.
If it does not seem like you can write code to answer the question, just return "I don't know" as the answer.
"""

base_prompt = hub.pull("langchain-ai/openai-functions-template")
prompt = base_prompt.partial(instructions=instructions)

In [120]:
agent = create_openai_functions_agent(ChatOpenAI(temperature=0), tools, prompt)

In [121]:
agent_executor = AgentExecutor(agent=agent, tools=tools, verbose=True)

In [135]:
bad_schema = """{
    "type": "object",
    "properties": {
        "name": {
            "type": "string"
        },
            "type": "number"
        }
    }
}
"""

try:
    json.loads(bad_schema)
except Exception as e:
    print(e)

agent_executor.invoke({
    "input": f"""Repair this json object: {bad_schema}""",
    "output": None,
    "code": None
})

Extra data: line 10 column 1 (char 147)



> Entering new AgentExecutor chain...
The JSON object you provided is not valid. The "type" property is duplicated within the "properties" object. To fix it, you can modify the JSON object as follows:

```json
{
    "type": "object",
    "properties": {
        "name": {
            "type": "string"
        },
        "age": {
            "type": "number"
        }
    }
}
```

In this fixed version, I assumed that you wanted to add an "age" property of type "number" to the "properties" object.

> Finished chain.


{'input': 'Repair this json object: {\n    "type": "object",\n    "properties": {\n        "name": {\n            "type": "string"\n        },\n            "type": "number"\n        }\n    }\n}\n',
 'output': 'The JSON object you provided is not valid. The "type" property is duplicated within the "properties" object. To fix it, you can modify the JSON object as follows:\n\n```json\n{\n    "type": "object",\n    "properties": {\n        "name": {\n            "type": "string"\n        },\n        "age": {\n            "type": "number"\n        }\n    }\n}\n```\n\nIn this fixed version, I assumed that you wanted to add an "age" property of type "number" to the "properties" object.',
 'code': None}

In [134]:
json.loads("""{\n    "type": "object",\n    "properties": {\n        "name": {\n            "type": "string"\n        },\n        "age": {\n            "type": "number"\n        }\n    }\n}""")

{'type': 'object',
 'properties': {'name': {'type': 'string'}, 'age': {'type': 'number'}}}